In [1]:
%load_ext autoreload
%autoreload 2
%matplotlib notebook

In [2]:
import geopandas as gpd
import pandas as pd
import pickle
import datetime

# Merge mortality and significance

## Mort

In [3]:
# Mortality results
moni_mort = gpd.read_file('./results/result_moni_mort_oct_15.geojson')
results_all = moni_mort.copy()

In [4]:
#results_all.loc[results_all.Country == 'United States']

## Sig

In [5]:
for sp in ['O3', 'NO2', 'PM2.5']:
    results_all.loc[:,f'Coefficient {sp}'] = 0
    results_all.loc[:,f'Coefficient {sp} 2.5'] = 0
    results_all.loc[:,f'Coefficient {sp} 97.5'] = 0
    results_all.loc[:,f'p value {sp}'] = 0

In [6]:
with open('./data/us_raw/stateabb.pkl', 'rb') as f:
    stateabb = pickle.load(f)
abbstates = {v: k for k,v in stateabb.items()}

In [7]:
# add sig results
regs = ['japan', 'korea', 'us', 'china', 'europe']
trads = {'japan': 'JP', 'korea': 'KR', 'us': 'US', 'china': 'CH', 
         'europe': 'EU'}
path ='/net/fs03/d1/gchossie/2020_aq/sarimax_models/'
for sp in ['O3', 'NO2', 'PM2.5']:
    for reg in regs:
        if reg == 'japan' and sp == 'O3':
            tmpsp = 'Ox'
        else:
            tmpsp = sp
        pathtmp = path + f'{reg}/results/{trads[reg]}_{tmpsp}.geojson'
        tmp = gpd.read_file(pathtmp)
        if reg == 'korea':
            tmp = tmp.rename(columns={'Coefficient loc': 'Coefficient',
                                     'Standard error loc': 'Standard error',
                                     'p value loc': 'p value'})
        tmp = tmp.rename(columns={'Coefficient': f'Coefficient {sp}',
                                     'p value': f'p value {sp}',
                                 'Standard error': f'Standard error {sp}'})
        lst = [f'Coefficient {sp}',f'p value {sp}', f'Standard error {sp}']
        tmp[lst] = tmp[lst].astype(float)
        if reg == 'us':
            tmp['Region'] = tmp['Region'].apply(lambda x: abbstates[x])
        for reg_loc in set(tmp['Region']):
            if len(tmp.loc[tmp['Region'] == reg_loc]) == 1:
                coeff = float(tmp.loc[tmp['Region'] == reg_loc, f'Coefficient {sp}'])
                pval = float(tmp.loc[tmp['Region'] == reg_loc, f'p value {sp}'])
                std = float(tmp.loc[tmp['Region'] == reg_loc, f'Standard error {sp}'])
                results_all.loc[results_all.Region == reg_loc, f'Coefficient {sp}'] =\
                    coeff
                results_all.loc[results_all.Region == reg_loc, f'p value {sp}'] =\
                    pval
                results_all.loc[results_all.Region == reg_loc, f'Coefficient {sp} 2.5'] =\
                    coeff - std*1.96
                results_all.loc[results_all.Region == reg_loc, f'Coefficient {sp} 97.5'] =\
                    coeff + std*1.96
            else:
                coeff = tmp.loc[tmp['Region'] == reg_loc, f'Coefficient {sp}'].values[0]
                pval = tmp.loc[tmp['Region'] == reg_loc, f'p value {sp}'].values[0]
                std = tmp.loc[tmp['Region'] == reg_loc, f'Standard error {sp}'].values[0]
                results_all.loc[results_all.Region == reg_loc, f'Coefficient {sp}'] =\
                    coeff
                results_all.loc[results_all.Region == reg_loc, f'p value {sp}'] =\
                    pval
                results_all.loc[results_all.Region == reg_loc, f'Coefficient {sp} 2.5'] =\
                    coeff - 1.96*std
                results_all.loc[results_all.Region == reg_loc, f'Coefficient {sp} 97.5'] =\
                    coeff + 1.96*std

## Time-avg, pop-wgt change in conc

In [8]:
for sp in ['O3', 'PM2.5', 'NO2']:
    results_all.loc[:,f'Actual {sp}'] = 0
    results_all.loc[:,f'Mean pred {sp}'] = 0
    results_all.loc[:,f'Low pred {sp}'] = 0
    results_all.loc[:,f'High pred {sp}'] = 0

In [9]:
for reg in set(results_all['Region']):
    country = results_all.loc[results_all['Region'] == reg,'Country'].values[0]
    if country == 'China':
        path= './data/ch_raw/prediction_sarimax/'
    elif country == 'Japan':
        path= './data/jp_raw/prediction_sarimax/'
    elif country == 'Korea':
        path= './data/kr_raw/prediction_sarimax/'
    elif country == 'United States':
        path= './data/us_raw/prediction_sarimax/'
    else:
        path = '/net/fs03/d1/gchossie/2020_aq/data/eu_raw/prediction_sarimax/'
    for sp in ['O3', 'PM2.5', 'NO2']:
        if country == 'United States':
            try:
                with open(path + f'preds_{reg}_{sp}_kriging.pkl', 'rb') as f:
                    preds = pickle.load(f)
            except: 
                continue
        else:
            try:
                with open(path + f'preds_{reg}_{sp}_kriging.pkl', 'rb') as f:
                    preds = pickle.load(f)
            except:
                continue
        if sp == 'NO2':
            preds = preds.rolling(7,axis=0).mean()
            preds = preds.loc[~pd.isnull(preds['Mean']),:]
        idx = results_all['Region'] == reg
        results_all.loc[idx,f'Actual {sp}'] = (preds['Actual']).mean() / results_all.loc[idx,'Population']
        results_all.loc[idx,f'Mean pred {sp}'] = (preds['Mean']).mean() / results_all.loc[idx,'Population']
        results_all.loc[idx,f'Low pred {sp}'] =(preds['Low']).mean() / results_all.loc[idx,'Population']
        results_all.loc[idx,f'High pred {sp}'] = (preds['High']).mean() / results_all.loc[idx,'Population']


In [10]:
for sp in ['NO2', 'PM2.5', 'O3']:
    results_all[f'Average rel {sp}'] = (results_all[f'Actual {sp}'] / results_all[f'Mean pred {sp}']) - 1

## Get validation results by region

In [11]:
r2s = pd.read_feather(f'arimax_pred_validation/validate_US.feather')
r2s['Country'] = r2s['Ensemble'] = 'United States'
for ens in ['China', 'Korea', 'Japan']:
    tmp = pd.read_feather(f'arimax_pred_validation/validate_{ens}.feather')
    tmp['Country'] = tmp['Ensemble'] = ens
    r2s = pd.concat([r2s, tmp], axis=0, ignore_index=True)

In [12]:
tmp = pd.read_feather(f'arimax_pred_validation/validate_Europe.feather')
def get_country(reg):
    return results_all.loc[results_all.Region == reg, 'Country'].values[0]
tmp['Ensemble'] = 'Europe'
tmp['Country'] = tmp['Region'].apply(get_country)

In [13]:
r2s = pd.concat([r2s, tmp], axis=0, ignore_index=True)

In [14]:
tmp_res = results_all.copy()

In [15]:
for sp in ['NO2', 'PM2.5', 'O3']:
    if sp == 'PM2.5': tmpsp = 'pm25'
    else: tmpsp = sp.lower()
    exec(f'r2s_{tmpsp} = r2s.loc[r2s.Species == "{sp}"]')
    exec(f'r2s_{tmpsp}.drop([c for c in r2s_{tmpsp}.columns if "daily" in c], axis=1, inplace=True)')
    lst_cols = [c]
    exec(f'tmp = r2s_{tmpsp}')
    tmp.rename(columns={c: c + f' {sp}' for c in lst_cols}, inplace=True)
    tmp.drop('Species', axis=1, inplace=True)
    tmp_res = pd.merge(tmp_res, tmp, on=['Ensemble', 'Country', 'Region'], how='left')
    tmp_res = tmp_res.drop_duplicates(subset=['Ensemble', 'Country', 'Region'])

/home/gchossie/anaconda3/envs/freight_us/lib/python3.8/site-packages/pandas/core/frame.py:4163: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


NameError: name 'c' is not defined

In [ ]:
results_all = tmp_res

## Mortality rate and export to Excel table


In [16]:
import numpy as np

In [17]:
raw = pd.read_pickle('./results/raw_mort_dist_oct_15.pkl')

In [18]:
# Create total mort rates with all significant mortalities
results_all.loc[:,'Mortality rate (per 1M)'] = 0
results_all.loc[:,'Mortality rate (per 1M) 2.5'] = 0
results_all.loc[:,'Mortality rate (per 1M) 97.5'] = 0
for idx in results_all.index:
    raw_dist = np.zeros((10000,))
    for sp in ['O3', 'NO2', 'PM2.5']:
        if ~np.isnan(results_all.loc[idx,f'{sp} mean']):# and results_all.loc[idx, f'p value {sp}'] <= 0.05:
            results_all.loc[idx,'Mortality rate (per 1M)'] +=\
                (1e6 * results_all.loc[idx,f'{sp} mean'] / results_all.loc[idx,f'Population'])
            raw_dist = raw_dist +\
                    raw[results_all.loc[idx, 'Country']][results_all.loc[idx, 'Region']][sp]
    results_all.loc[idx,'Mortality rate (per 1M) 2.5'] =\
        (1e6 * np.percentile(raw_dist, 2.5) / results_all.loc[idx,f'Population'])
    results_all.loc[idx,'Mortality rate (per 1M) 97.5'] =\
        (1e6 * np.percentile(raw_dist, 97.5) / results_all.loc[idx,f'Population'])

<ipython-input-18-e0a3f0fd4507>:10: RuntimeWarning: invalid value encountered in double_scalars
  (1e6 * results_all.loc[idx,f'{sp} mean'] / results_all.loc[idx,f'Population'])
<ipython-input-18-e0a3f0fd4507>:14: RuntimeWarning: invalid value encountered in double_scalars
  (1e6 * np.percentile(raw_dist, 2.5) / results_all.loc[idx,f'Population'])
<ipython-input-18-e0a3f0fd4507>:16: RuntimeWarning: invalid value encountered in double_scalars
  (1e6 * np.percentile(raw_dist, 97.5) / results_all.loc[idx,f'Population'])


In [19]:
results_all.head(2)

Ensemble Country Region  Population    NO2 mean     NO2 2.5   NO2 97.5  \
0    Japan   Japan  Aichi   7220143.5   -7.138536  -14.812099   0.527584   
1    Japan   Japan  Osaka   8177242.0 -130.492185 -270.700359  10.086240   

   PM2.5 mean   PM2.5 2.5  PM2.5 97.5  ...  Actual NO2  Mean pred NO2  \
0 -119.771086 -180.429434  -59.912951  ...   20.468311      20.877874   
1 -141.666251 -214.014994  -70.061279  ...   25.624244      31.515562   

   Low pred NO2 High pred NO2  Average rel NO2  Average rel PM2.5  \
0    -20.622776     62.378525        -0.019617          -0.287145   
1     16.217937     46.813186        -0.186934          -0.241187   

   Average rel O3  Mortality rate (per 1M)  Mortality rate (per 1M) 2.5  \
0        0.157411                -6.848623                   -11.539154   
1        0.131356               -23.121160                   -43.953566   

   Mortality rate (per 1M) 97.5  
0                     -2.711731  
1                     -2.338407  

[2 rows x 44 columns]

In [ ]:
tdy = datetime.datetime.today().strftime(format='%b_%d').lower()
results_all.to_file(f'./results/results_all_{tdy}.geojson',driver='GeoJSON')

In [ ]:
results_all = gpd.read_file(f'./results/results_all_{tdy}.geojson')

In [ ]:
'r2 monthly', 'RMSE monthly', 'Median abs monthly', 'Average_true'

In [ ]:
res_all = results_all[['Ensemble', 'Country', 'Region', 
                           'Mortality rate (per 1M)', 'Mortality rate (per 1M) 2.5', 
                           'Mortality rate (per 1M) 97.5',
                          'p value NO2', 'Coefficient NO2', 'Coefficient NO2 2.5', 'Coefficient NO2 97.5',
                          'NO2 mean', 'NO2 2.5', 'NO2 97.5', 
                          'Average rel NO2', 'r2 monthly NO2', 'RMSE monthly NO2', 
                          'Median abs monthly NO2', 'Average_true NO2',
                          'p value PM2.5', 'Coefficient PM2.5', 'Coefficient PM2.5 2.5', 'Coefficient PM2.5 97.5',
                          'PM2.5 mean', 'PM2.5 2.5', 'PM2.5 97.5',
                          'Average rel PM2.5', 'r2 monthly PM2.5', 'RMSE monthly PM2.5', 
                          'Median abs monthly PM2.5', 'Average_true PM2.5',
                          'p value O3', 'Coefficient O3', 'Coefficient O3 2.5', 'Coefficient O3 97.5',
                          'O3 mean', 'O3 2.5', 'O3 97.5',
                          'Average rel O3', 'r2 monthly O3', 'RMSE monthly O3', 
                          'Median abs monthly O3', 'Average_true O3',
                          'geometry']]
res_all = res_all.sort_values(by=['Country', 'Region'])

In [ ]:
res_all.drop('geometry',axis=1, inplace=True)

In [ ]:
res_all.sort_values(by=['Country', 'Region']).to_excel(f'./results/moni_all_{tdy}.xlsx')

In [ ]:
res_all.sort_values(by=['Country', 'Region']).columns

### Region-level analysis for paper

In [ ]:
# List of regions with decreases in NO2 across methods
dec_no2_moni = results_all.loc[pd.notnull(results_all.Ensemble).values *\
                (results_all['Coefficient NO2'] <= 0).values, 'Region'].values
dec_no2_satmoni = pd.read_csv('results/tmp_satmoni.csv').Region.values
dec_no2_satnow = pd.read_csv('results/tmp_satnow.csv').Region.values

In [ ]:
# List of regions with stat sif change in both PM and NO2
len(results_all.loc[(results_all['Coefficient NO2'] <= 0).values *\
                    (results_all['p value NO2'] <= 0.05).values *\
                    (results_all['p value PM2.5'] <= 0.05).values *\
                    (results_all['Coefficient PM2.5'] <= 0).values])

In [ ]:
# List of regions with decreases in all 3 pollutants
results_all.loc[(results_all['Coefficient NO2'] <= 0).values *\
                    (results_all['Coefficient O3'] <= 0).values *\
                (results_all['Coefficient PM2.5'] <= 0).values].groupby('Ensemble').count()

In [ ]:
# Compute average change in pollutant from testing ARIMA with 95% CI
sp = 'O3'
if sp != 'PM2.5': tmpsp=sp.lower()
else: tmpsp = 'pm25'
tmp = results_all.query('Ensemble == "United States"').rename(columns={f'p value {sp}': f'p_value_{tmpsp}'})
#tmp = tmp.query(f'p_value_{tmpsp} <= 0.05')
tmp.drop(tmp.query('Region in ["Valle d\'Aosta", "Slovakia", "Turkey"]').index, inplace=True)
(tmp[f'Coefficient {sp} 97.5'] * tmp['Population']).sum() * si / tmp['Population'].sum()

In [ ]:
_ / ((tmp[f'Mean pred {sp}'] * tmp['Population']).sum() / tmp['Population'].sum())

In [ ]:
tmp.loc[tmp[f'Coefficient {sp} 2.5'] < -1]

In [ ]:
results_all

# Plot

In [ ]:
import sys

In [ ]:
sys.path.insert(1,'../sat_moni/')

In [ ]:
results_all = gpd.read_file('./results/results_all.geojson')

In [ ]:
from plotting_utilities import *

In [ ]:
plot_all(results_all, 'US', sp='NO2', sig_only=True)

In [ ]:
results_all.columns

In [ ]:
idxpop = results_all.Ensemble.apply(lambda x: x in ['China']).values
idx = (results_all['p value PM2.5'] <= 0.05).values * idxpop
results_all.loc[idx,'PM2.5 mean'].sum()# * results_all.loc[idx,'Population']).sum() / results_all.loc[idx,'Population'].sum()

In [ ]:
results_all.loc[results_all['p value PM2.5'] <= 0.05,'PM2.5 mean'].sum()

In [ ]:
len(results_all.loc[idx]), len(results_all.loc[idxpop])

In [ ]:
sp = 'PM2.5'
sig[f'Coefficient {sp}'].min(),sig[f'Coefficient {sp}'].max()

# Get 95% CI by country

In [ ]:
tdy = datetime.datetime.today().strftime(format='%b_%d').lower()

In [ ]:
!ls results/results_all_*.geojson

In [3]:
results_all = gpd.read_file(f'./results/results_all_oct_15.geojson')

In [ ]:
tmp = results_all.query('Ensemble == "United States"')

In [ ]:
(tmp['Average rel NO2'] * tmp['Population']).sum() / tmp['Population'].sum()

In [ ]:
tmp = results[['Ensemble', 'Country', 'Region']]
tmp['']

In [ ]:
#results_all.groupby('Country')['Population'].sum().to_csv('./results/country_pop.csv')

In [5]:
with open('./results/raw_mort_dist_oct_21_sens.pkl','rb') as f:
    raw = pickle.load(f)
#raw_cf = pd.read_pickle('results/raw_mort_dist_jul9_counterfactual.pkl')

In [9]:
countries = list(set(results_all.Country))

In [6]:
import numpy as np

In [7]:
def get_res_by_country(country, sp='NO2', cause='All', stat_sig_only=True):
    '''sp can be NO2, O3, PM2.5 or all
    Cause can be 'All', 'Cardiovascular', 'Respiratory', or 'Cause_spec'
    '''
    causes = {'All': ['All causes'], 'Cardiovascular': ['Cardiovascular diseases'],
             'Respiratory': ['Lower respiratory infections',
                      'Upper respiratory infections',
                      'Chronic respiratory diseases'],
             'Cause_spec': ['Cardiovascular diseases', 
                            'Lower respiratory infections',
                            'Upper respiratory infections',
                            'Chronic respiratory diseases']}
    if stat_sig_only:
        # Get subset of results where we have significant mortality results
        lst_sig = {}
        lst_sig['PM2.5'] = set(results_all.loc[results_all['p value PM2.5'] <= 0.05,'Region'])
        lst_sig['NO2'] = set(results_all.loc[results_all['p value NO2'] <= 0.05,'Region'])
        lst_sig['O3'] = set(results_all.loc[results_all['p value O3'] <= 0.05,'Region'])
    else:
        lst_sig = {}
        lst_sig['PM2.5'] = lst_sig['NO2'] = lst_sig['O3'] = set(results_all.Region)
    
    eu_countries = [c for c in countries if c not in ['United States', 'China',
                                                      'Korea', 'Japan']]
    if country not in ['Europe', 'all']:
        idx = results_all.Country == country
        idxpop = (results_all.Country == country).values * \
            (results_all['Mortality rate (per 1M)'] != 0).values
    elif country == 'Europe':
        idx = results_all.Ensemble == country
        idxpop = (results_all.Ensemble == country).values * \
            (results_all['Mortality rate (per 1M)'] != 0).values
    else:
        idx = results_all.index
        idxpop = results_all['Mortality rate (per 1M)'] != 0
    pop = results_all.loc[idxpop, 'Population'].sum()
    if sp == 'all':
        if country not in ['Europe', 'all']:
            dist = np.sum([raw[country][reg]['PM2.5'][c] for c in causes[cause] for reg in raw[country].keys() if reg in lst_sig['PM2.5']], axis=0) +\
                np.sum([raw[country][reg]['NO2'][c] for c in causes[cause] for reg in raw[country].keys() if reg in lst_sig['NO2']], axis=0) +\
                np.sum([raw[country][reg]['O3'][c] for c in causes[cause] for reg in raw[country].keys() if reg in lst_sig['O3']], axis=0)
        elif country == 'Europe':
            dist = np.sum([raw[ctr][reg]['PM2.5'][c] for c in causes[cause] for ctr in eu_countries for reg in raw[ctr].keys() if reg in lst_sig['PM2.5']], axis=0) +\
                np.sum([raw[ctr][reg]['NO2'][c] for c in causes[cause] for ctr in eu_countries for reg in raw[ctr].keys() if reg in lst_sig['NO2']], axis=0) +\
                np.sum([raw[ctr][reg]['O3'][c] for c in causes[cause] for ctr in eu_countries for reg in raw[ctr].keys() if reg in lst_sig['O3']], axis=0)
        else:
            dist = np.sum([raw[ctr][reg]['PM2.5'][c] for c in causes[cause] for ctr in countries for reg in raw[ctr].keys() if reg in lst_sig['PM2.5']], axis=0) +\
                np.sum([raw[ctr][reg]['NO2'][c] for c in causes[cause] for ctr in countries for reg in raw[ctr].keys() if reg in lst_sig['NO2']], axis=0) +\
                np.sum([raw[ctr][reg]['O3'][c] for c in causes[cause] for ctr in countries for reg in raw[ctr].keys() if reg in lst_sig['O3']], axis=0)
    else:
        if country not in ['Europe', 'all']:
            dist = np.sum([raw[country][reg][sp][c] for c in causes[cause] for reg in raw[country].keys() if reg in lst_sig[sp]], axis=0)
        elif country == 'Europe':
            dist = np.sum([raw[ctr][reg][sp][c] for c in causes[cause] for ctr in eu_countries for reg in raw[ctr].keys() if reg in lst_sig[sp]], axis=0)
        else:
            dist = np.sum([raw[ctr][reg][sp][c] for c in causes[cause] for ctr in countries for reg in raw[ctr].keys() if reg in lst_sig[sp]], axis=0)
    mean = np.mean(dist)
    low = np.percentile(dist, 2.5)
    med = np.percentile(dist, 50)
    high = np.percentile(dist, 97.5)
    return [mean, low, med, high, pop]

In [ ]:
def get_res_cf_by_country(country, sp='NO2'):
    '''sp can be NO2, O3, PM2.5 or all'''
    eu_countries = [c for c in countries if c not in ['United States', 'China',
                                                      'Korea', 'Japan']]
    if country not in ['Europe', 'all']:
        idx = results_all.Country == country
        idxpop = (results_all.Country == country).values * \
            (results_all['Mortality rate (per 1M)'] != 0).values
    elif country == 'Europe':
        idx = results_all.Ensemble == country
        idxpop = (results_all.Ensemble == country).values * \
            (results_all['Mortality rate (per 1M)'] != 0).values
    else:
        idx = results_all.index
        idxpop = results_all['Mortality rate (per 1M)'] != 0
    pop = results_all.loc[idxpop, 'Population'].sum()
    if sp == 'all':
        if country not in ['Europe', 'all']:
            dist = np.sum([raw_cf[country][reg]['PM2.5'] for reg in raw_cf[country].keys() if reg in lst_sig['PM2.5']], axis=0) +\
                np.sum([raw_cf[country][reg]['NO2'] for reg in raw_cf[country].keys() if reg in lst_sig['NO2']], axis=0) +\
                np.sum([raw_cf[country][reg]['O3'] for reg in raw_cf[country].keys() if reg in lst_sig['O3']], axis=0)
        elif country == 'Europe':
            dist = np.sum([raw_cf[ctr][reg]['PM2.5'] for ctr in eu_countries for reg in raw_cf[ctr].keys() if reg in lst_sig['PM2.5']], axis=0) +\
                np.sum([raw_cf[ctr][reg]['NO2'] for ctr in eu_countries for reg in raw_cf[ctr].keys() if reg in lst_sig['NO2']], axis=0) +\
                np.sum([raw_cf[ctr][reg]['O3'] for ctr in eu_countries for reg in raw_cf[ctr].keys() if reg in lst_sig['O3']], axis=0)
        else:
            dist = np.sum([raw_cf[ctr][reg]['PM2.5'] for ctr in countries for reg in raw_cf[ctr].keys() if reg in lst_sig['PM2.5']], axis=0) +\
                np.sum([raw_cf[ctr][reg]['NO2'] for ctr in countries for reg in raw_cf[ctr].keys() if reg in lst_sig['NO2']], axis=0) +\
                np.sum([raw_cf[ctr][reg]['O3'] for ctr in countries for reg in raw_cf[ctr].keys() if reg in lst_sig['O3']], axis=0)
    else:
        if country not in ['Europe', 'all']:
            dist = np.sum([raw_cf[country][reg][sp]
                           for reg in raw_cf[country].keys() if reg in lst_sig[sp]], axis=0)
        elif country == 'Europe':
            dist = np.sum([raw_cf[ctr][reg][sp]
                           for ctr in eu_countries for reg in raw_cf[ctr].keys() if reg in lst_sig[sp]], axis=0)
        else:
            dist = np.sum([raw_cf[ctr][reg][sp]
                           for ctr in countries for reg in raw_cf[ctr].keys() if reg in lst_sig[sp]], axis=0)
    mean = np.mean(dist)
    low = np.percentile(dist, 2.5)
    med = np.percentile(dist, 50)
    high = np.percentile(dist, 97.5)
    return [mean, low, med, high, pop]

In [ ]:
import numpy as np

In [12]:
country_res = pd.DataFrame(index=countries + ['Europe', 'all'],columns=['mean', '2.5', '50', '97.5',
                                                   'Population'],
                           dtype=float)
sp = 'NO2'
for cause in ['All', 'Cardiovascular', 'Respiratory', 'Cause_spec']:
    for country in countries:
        country_res.loc[country,['mean', '2.5', '50', '97.5','Population']] =\
            get_res_by_country(country, sp=sp, cause=cause, stat_sig_only=False)
        #country_res.loc[country, 'cf'] = get_res_cf_by_country(country, sp=sp)[0]
    country_res.loc['Europe',['mean', '2.5', '50', '97.5','Population']] =\
        get_res_by_country('Europe', sp=sp, cause=cause, stat_sig_only=False)
    #country_res.loc['Europe', 'cf'] = get_res_cf_by_country('Europe', sp=sp)[0]
    country_res.loc['all',['mean', '2.5', '50', '97.5','Population']] =\
        get_res_by_country('all', sp=sp, cause=cause, stat_sig_only=False)
    #country_res.loc['all', 'cf'] = get_res_cf_by_country('all', sp=sp)[0]
    exec(f'{cause} = country_res.dropna(axis=0).sort_values(by="mean")')

/home/gchossie/anaconda3/envs/freight_us/lib/python3.8/site-packages/numpy/core/fromnumeric.py:87: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)
/home/gchossie/anaconda3/envs/freight_us/lib/python3.8/site-packages/numpy/core/fromnumeric.py:87: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)
/home/gchossie/anaconda3/envs/freight_us/lib/python3.8/site-packages/numpy/core/fromnumeric.py:87: VisibleDeprecationWarning: Creating an ndarray from rag

In [13]:
All

mean           2.5            50  \
all                    -50712.574524 -62047.164314 -50688.858727   
China                  -33094.153696 -40485.020724 -33084.597598   
Europe                 -10492.452902 -12858.556872 -10489.219301   
United States           -3438.722501  -4200.152737  -3437.610792   
Japan                   -2714.733099  -3319.960807  -2711.640017   
Germany                 -2387.219181  -2927.002655  -2385.972611   
United Kingdom          -1928.622363  -2358.915367  -1927.072771   
Italy                   -1594.620914  -1952.395509  -1593.807278   
France                  -1441.735139  -1762.323498  -1441.727347   
Korea                    -972.512327  -1191.426551   -972.391325   
Spain                    -853.633557  -1044.940085   -853.184213   
Poland                   -516.160232   -632.945341   -515.608715   
Belgium                  -266.706932   -328.494551   -266.408031   
Netherlands              -223.645871   -276.226073   -223.455769   
Greece                   -186.759442   -229.419122   -186.708831   
Czechia                  -155.570412   -191.370884   -155.442776   
Austria                  -107.420509   -132.215506   -107.324539   
Switzerland               -94.136454   -115.763997    -94.157679   
Finland                   -87.205451   -107.408054    -87.149316   
Norway                    -83.649747   -102.275984    -83.614512   
Sweden                    -81.764745   -100.423473    -81.692051   
Portugal                  -80.973715    -99.602304    -80.953611   
Croatia                   -77.098318    -95.008918    -76.982222   
Slovakia                  -69.994379    -86.116054    -69.935671   
Denmark                   -63.555203    -78.315322    -63.430427   
Ireland                   -48.710692    -59.841206    -48.664548   
Hungary                   -38.607172    -47.253082    -38.575688   
Romania                   -35.199377    -43.168869    -35.172123   
Bulgaria                  -29.156737    -35.764733    -29.114234   
Slovenia                  -25.705907    -31.814602    -25.664251   
Estonia                   -11.382992    -14.212913    -11.354848   
Luxembourg                 -5.442782     -6.716569     -5.440465   
Iceland                    -2.001393     -2.452608     -2.000346   
Andorra                    -1.000166     -1.245587     -0.999563   
Cyprus                      0.000000      0.000000      0.000000   
Turkey                      0.000000      0.000000      0.000000   
Bosnia and Herzegovina      5.226881      4.047613      5.222149   

                                97.5    Population  
all                    -39550.543747  2.356438e+09  
China                  -25809.674594  1.367635e+09  
Europe                  -8176.021230  5.038635e+08  
United States           -2678.678587  3.152431e+08  
Japan                   -2114.759643  1.207478e+08  
Germany                 -1851.904397  8.053359e+07  
United Kingdom          -1502.055549  6.311466e+07  
Italy                   -1242.813531  5.780893e+07  
France                  -1118.931047  6.351449e+07  
Korea                    -757.157329  4.894908e+07  
Spain                    -664.426398  4.243308e+07  
Poland                   -400.519231  3.859604e+07  
Belgium                  -207.285167  1.128374e+07  
Netherlands              -173.427385  1.665828e+07  
Greece                   -144.241923  9.988486e+06  
Czechia                  -120.523671  1.052993e+07  
Austria                   -83.326686  8.593058e+06  
Switzerland               -72.739199  8.199810e+06  
Finland                   -67.375761  5.192258e+06  
Norway                    -65.157480  4.634442e+06  
Sweden                    -63.587489  9.285870e+06  
Portugal                  -62.869783  9.777071e+06  
Croatia                   -59.931105  4.023400e+06  
Slovakia                  -54.241661  5.401158e+06  
Denmark                   -49.300794  5.249530e+06  
Ireland                   -37.726189  4.506282e+06  
Hungary         

In [39]:
Cardiovascular

mean           2.5            50  \
all                    -37587.181355 -49942.032136 -37572.329700   
China                  -32747.668670 -43515.790826 -32738.339786   
Europe                  -3395.505656  -4512.211661  -3392.450984   
Germany                  -900.075374  -1197.527763   -899.828031   
Japan                    -794.861626  -1058.009020   -794.469155   
Poland                   -641.539695   -853.539178   -640.992971   
United States            -329.917205   -438.337719   -330.241995   
Korea                    -319.228199   -425.116856   -319.280268   
Italy                    -312.249224   -414.325595   -312.034489   
Romania                  -259.154716   -345.089826   -258.912662   
Czechia                  -198.449574   -265.207917   -198.054079   
United Kingdom           -183.840883   -244.514210   -183.788372   
France                   -170.713936   -226.491800   -170.621103   
Greece                   -105.334808   -140.610547   -105.231469   
Spain                     -98.819378   -131.077971    -98.750515   
Bosnia and Herzegovina    -85.231265   -113.639162    -85.223633   
Croatia                   -76.788498   -102.247364    -76.731601   
Belgium                   -71.484016    -95.426895    -71.352325   
Bulgaria                  -63.850799    -85.144822    -63.809901   
Slovakia                  -63.376122    -84.882582    -63.256335   
Netherlands               -45.471840    -60.787313    -45.469042   
Austria                   -29.119499    -39.017863    -29.070786   
Denmark                   -17.822929    -23.768818    -17.802028   
Sweden                    -16.133308    -21.543658    -16.124009   
Finland                   -11.400843    -15.206250    -11.404587   
Portugal                   -9.713122    -12.941027     -9.704774   
Switzerland                -9.331384    -12.473018     -9.323140   
Norway                     -8.368186    -11.133014     -8.357567   
Hungary                    -5.886205     -7.855860     -5.886502   
Ireland                    -5.020239     -6.706901     -5.016207   
Slovenia                   -4.830556     -6.460222     -4.820967   
Estonia                    -1.574093     -2.132051     -1.570292   
Luxembourg                 -0.392814     -0.529812     -0.392181   
Andorra                    -0.139439     -0.188615     -0.139193   
Turkey                      0.000000      0.000000      0.000000   
Cyprus                      0.000000      0.000000      0.000000   
Iceland                     0.607090      0.404025      0.606915   

                                97.5    Population  
all                    -25146.323444  2.356438e+09  
China                  -21901.437619  1.367635e+09  
Europe                  -2267.187920  5.038635e+08  
Germany                  -598.278139  8.053359e+07  
Japan                    -530.131757  1.207478e+08  
Poland                   -426.542071  3.859604e+07  
United States            -219.274018  3.152431e+08  
Korea                    -212.515684  4.894908e+07  
Italy                    -208.505113  5.780893e+07  
Romania                  -172.558410  1.936143e+07  
Czechia                  -131.866261  1.052993e+07  
United Kingdom           -122.987868  6.311466e+07  
France                   -113.972723  6.351449e+07  
Greece                    -69.875000  9.988486e+06  
Spain                     -65.902978  4.243308e+07  
Bosnia and Herzegovina    -56.784707  3.854267e+06  
Croatia                   -51.139229  4.023400e+06  
Belgium                   -47.554985  1.128374e+07  
Bulgaria                  -42.486619  7.209300e+06  
Slovakia                  -42.082313  5.401158e+06  
Netherlands               -30.188855  1.665828e+07  
Austria                   -19.359381  8.593058e+06  
Denmark                   -11.819920  5.249530e+06  
Sweden                    -10.755763  9.285870e+06  
Finland                    -7.600585  5.192258e+06  
Portugal                   -6.456535  9.777071e+06  
Switzerland     

In [ ]:
Cardiovascular.loc['all', 'mean'] / Cause_spec.loc['all', 'mean']

In [ ]:
(Cause_spec).sort_values(by='mean')

In [ ]:
(Cardiovascular/All)['mean'].mean()

In [ ]:
(Respiratory/All)['mean'].mean()

# Get stringency and results per std of index

In [ ]:
# Get Oxford stringency
stringency = pd.read_csv('https://github.com/OxCGRT/covid-policy-tracker/raw/master/data/OxCGRT_latest.csv',
                  parse_dates=['Date'])
stringency = stringency[['CountryName', 'CountryCode', 'Date', 'C1_School closing',
           'C2_Workplace closing', 'C3_Cancel public events',
           'C4_Restrictions on gatherings', 'C5_Close public transport',
           'C6_Stay at home requirements', 'C7_Restrictions on internal movement',
           'C8_International travel controls', 'H1_Public information campaigns',
           'StringencyIndex']]
stringency = stringency.fillna(method='pad')
stringency = pd.pivot_table(stringency, values='StringencyIndex', index='Date',
                     columns='CountryName')
stringency = stringency.loc[stringency.index <= pd.to_datetime('20200706')]

In [ ]:
stringency.to_pickle('data/shutdown_index_jul_6.pkl')

In [ ]:
stringency = pd.read_pickle('data/shutdown_index_jul_6.pkl')

In [ ]:
# Add to table
#res_all.loc[:, 'Average stringency'] = 0
tmp = pd.DataFrame(index=country_res.index)
for country in country_res.index:
    if country == 'all' or country == 'Europe': 
        continue
    elif country == 'Korea': 
        tmpcountry = 'South Korea'
    elif country == 'Slovakia':
        tmpcountry = 'Slovak Republic'
    elif country == 'Czechia':
        tmpcountry = 'Czech Republic'
    else:
        tmpcountry = country
    country_res.loc[country, 'Average stringency'] = stringency[tmpcountry].loc[stringency[tmpcountry]>0].mean()

In [ ]:
country_res['Average stringency'].to_pickle('data/average_str.pickle')

In [ ]:
country_res.rename(columns={'Population': 'Affected population'}, inplace=True)
country_res['Population'] = 0
for ctr in country_res.index:
    try:
        country_res.loc[ctr, 'Population'] = results_all.groupby('Country').sum().loc[ctr,'Population']
    except:
        pass

In [ ]:
country_res = country_res.reset_index().rename(columns={'index': 'Country'})

In [ ]:
def get_ensemble(ctr):
    if ctr == 'all' or ctr == 'Europe': return None
    else:
        return results_all.query(f'Country == "{ctr}"')['Ensemble'].values[0]

In [ ]:
country_res['norm mort'] = 1e6 * country_res['mean'] / country_res['Population']
country_res['Ensemble'] = country_res['Country'].apply(get_ensemble)

In [ ]:
lst = ['Europe', 'United States']
#lst = ['China', 'Japan', 'Korea']
country_res.query(f'Ensemble in {lst}')[['norm mort', 'Average stringency']].corr()**2

In [ ]:
country_res.query(f'Ensemble in {lst}').plot.scatter(x='Average stringency', y='norm mort')

In [ ]:
tmp.drop('Affected population', axis=1).to_csv('results/monitors_by_country_10-9.csv')

In [ ]:
country_res.dropna(axis=0).sort_values(by='mean').to_csv(f'results/{sp.lower()}.csv')

In [ ]:
# Get lockdown stringency index std
res_with_std = results_all.copy()
res_with_std.loc[:, 'Std stringency'] = 0
for country in set(res_with_std.Country):
    if country == 'all' or country == 'Europe': 
        continue
    elif country == 'Korea': 
        tmpcountry = 'South Korea'
    elif country == 'Slovakia':
        tmpcountry = 'Slovak Republic'
    elif country == 'Czechia':
        tmpcountry = 'Czech Republic'
    else:
        tmpcountry = country
    res_with_std.loc[res_with_std.Country == country, 'Std stringency'] = stringency[tmpcountry].loc[stringency[tmpcountry]>0].dropna().std()

In [ ]:
tmp['Coefficient PM2.5']

In [ ]:
sp = 'pm25'
if sp != 'pm25':
    spp = sp.upper()
else:
    spp = 'PM2.5'
ens = 'Japan'
tmp = res_with_std.query(f'Ensemble == "{ens}"').rename(columns={'p value NO2': 'p_value_no2',
                                                                 'p value O3': 'p_value_o3',
                                                                 'p value PM2.5': 'p_value_pm25'})
tmpp = tmp.query(f'p_value_{sp} <= 0.05')[
    ['Region', 'Std stringency', 'Population'] + [n for n in tmp.columns if spp in n]]
for quant in ['', ' 2.5', ' 97.5']:
    tmpp['Coeff' + quant] = tmpp[f'Coefficient {spp}' + quant] * tmpp[f'Std stringency']
(tmpp['Population'] * tmpp['Coeff']).sum() / (tmpp['Population']).sum()

In [ ]:
country_res.dropna(axis=0).sort_values(by='mean')

In [ ]:
country_res.dropna(axis=0).sort_values(by='mean').to_csv(f'./results/monitors_by_country_{sp}_{tdy}.csv')

In [ ]:
results_all.loc[results_all['Mortality rate (per 1M)'] > 0]

# Normalize by counterfactual mortalities

In [ ]:
!ls results/*_counterfactual.geojson

In [ ]:
#results_all = gpd.read_file('./results/results_all.geojson')
cf_mort = gpd.read_file('./results/result_moni_mort_jul3_counterfactual.geojson')

In [ ]:
cf_mort.drop([f'{sp} 2.5' for sp in ['NO2', 'PM2.5', 'O3']],axis=1, inplace=True)

In [ ]:
cf_mort.drop([f'{sp} 97.5' for sp in ['NO2', 'PM2.5', 'O3']],axis=1, inplace=True)

In [ ]:
cf_mort.drop('geometry',axis=1, inplace=True); cf_mort.head(2)

In [ ]:
cf_mort['Mortality_cf'] = cf_mort[['NO2 mean','PM2.5 mean','O3 mean']].sum(axis=1)

In [ ]:
results_all.loc[:, 'Mortality'] = results_all['Mortality rate (per 1M)'] * 1e-6 *\
                                      results_all['Population']

In [ ]:
tmp = pd.merge(results_all[['Country', 'Region', 'Population', 'Mortality']],
         cf_mort[['Region', 'Mortality_cf']], on='Region'); tmp

In [ ]:
tmp.loc[:,'Ratio'] = (tmp['Mortality'] / tmp['Mortality_cf']) * tmp['Population']
pop_country = tmp[['Country', 'Population']].groupby('Country').sum().rename(columns={'Population': 'Ratio'})
out = tmp[['Country', 'Ratio']].groupby('Country').sum() / pop_country
out = out.loc[out['Ratio'] != 0]; out.to_csv('ratio_mort_covid_tot_aq_mort.csv')

In [ ]:
# Get average stringency
with open('./data/shutdown_index.pkl', 'rb') as f:
    sd = pickle.load(f)

In [ ]:
import pycountry

In [ ]:
sd = sd.rename(columns={col: pycountry.countries.get(alpha_3=col).name for col in sd.columns})
sd = sd.rename(columns={'Korea, Republic of': 'Korea'})

In [ ]:
out.head(1)

In [ ]:
out.loc[:, 'Average stringency'] = 0
sd = sd.loc[sd.index <= pd.to_datetime('20200520')]
for idx in out.index:
    avg = sd[idx].loc[sd[idx] >= 0].mean()
    out.loc[idx,'Average stringency'] = avg
out['Ratio'] *= -1

In [ ]:
out.drop('Andorra',axis=0).to_csv('ratio_mort_covid_tot_aq_mort.csv')

In [ ]:
import scipy.stats

In [ ]:
tmp = out.drop('Andorra',axis=0)

In [ ]:
scipy.stats.linregress(tmp['Average stringency'], tmp['Ratio'])

In [ ]:
tmp.plot.scatter('Average stringency', 'Ratio')

# Get COVID mort

In [ ]:
import requests

In [ ]:
url = 'https://github.com/CSSEGISandData/COVID-19/blob/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_global.csv'
resp = requests.get(url)
#covid_deaths = pd.read_csv('https://github.com/CSSEGISandData/COVID-19/blob/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_global.csv')

In [ ]:
mort = pd.read_html(resp.content)[0]

In [ ]:
mort.loc[mort['Country/Region'].apply(lambda x: x in set(results_all.Country))]['7/6/20'].sum()+\
    mort.loc[mort['Country/Region'] == 'US']['7/6/20'].sum() +\
    mort.loc[mort['Country/Region'] == 'Korea, South']['7/6/20'].sum()

In [ ]:
mort.loc[mort['Country/Region'].apply(lambda x: x in set(results_all.loc[results_all.Ensemble == 'Europe', 'Country']))]['7/6/20'].sum()

In [ ]:
mort.loc[mort['Country/Region'] == 'China']['7/6/20'].sum()

In [ ]:
mort['7/7/20'].sum()

In [ ]:
mort[['Country/Region','7/7/20']].sort_values(by='7/7/20',ascending=False).head(15)

In [ ]:
mort[['Country/Region','5/20/20']].sort_values(by='5/20/20',ascending=False).sum()